In [1]:
import numpy as np
import matplotlib.pyplot as plt
from sklearn.neighbors import NearestNeighbors
import pandas as pd
import seaborn as sns
from statsmodels import api as sm
from matplotlib import pyplot as plt
from pandas.plotting import register_matplotlib_converters
import os
import numpy as np
import validate
from sklearn.decomposition import PCA
from sklearn.neighbors import LocalOutlierFactor
import math
import sys

In [2]:
data_dir='fixed_csv_label_ver2'
original = pd.read_csv( os.path.join(data_dir, 'learning_data_10.csv') )
df = pd.read_csv( os.path.join(data_dir, 'learning_data_10.csv') )
df=df[df['day']<=9]
df

original  label  time  day
0            53.4      0    15    0
1            52.8      0    15    0
2            52.8      0    15    0
3            53.2      0    15    0
4            53.6      0    15    0
...           ...    ...   ...  ...
3995345      45.9      0     5    9
3995346      45.6      0     5    9
3995347      45.8      0     5    9
3995348      45.7      0     5    9
3995349      45.9      0     5    9

[3995350 rows x 4 columns]

In [3]:
def make_data(x, str,w):
    x=pd.DataFrame(x)
    window=w
    for i in range(1, window):
        column=f'{str}_lag{i}'
        x[column]=x[str].shift(i)
    return x

def make_label(x, w):
    window=w
    x['label_all']=x['label']
    for i in range(1, window):
        x.loc[(x['label_all']==1)|(x['label'].shift(i)==1), 'label_all']=1
        x.loc[(x['label_all']==0)&(x['label'].shift(i)==0), 'label_all']=0
    
    x['label']=x['label_all']
    return x[['label']]

df_list=[]
for i in set(df['day']):
    lag=[] 
    window=5
    lag.append(make_data(df.loc[df['day']==i, ['original']], 'original', window))
    lag.append(df.loc[df['day']==i, ['day']])
    lag.append(make_label(df.loc[df['day']==i, ['label']], window))
    df_add_lag=pd.concat(lag, axis=1)
    df_list.append(df_add_lag)
df=pd.concat(df_list)
df=df.dropna().reset_index(drop=True)
df

original  original_lag1  original_lag2  original_lag3  original_lag4  \
0            53.6           53.2           52.8           52.8           53.4   
1            54.0           53.6           53.2           52.8           52.8   
2            54.7           54.0           53.6           53.2           52.8   
3            55.7           54.7           54.0           53.6           53.2   
4            55.5           55.7           54.7           54.0           53.6   
...           ...            ...            ...            ...            ...   
3995305      45.9           45.6           45.4           45.9           46.0   
3995306      45.6           45.9           45.6           45.4           45.9   
3995307      45.8           45.6           45.9           45.6           45.4   
3995308      45.7           45.8           45.6           45.9           45.6   
3995309      45.9           45.7           45.8           45.6           45.9   

         day  label  
0          0      0  
1          0      0  
2          0      0  
3          0      0  
4          0      0  
...      ...    ...  
3995305    9      0  
3995306    9      0  
3995307    9      0  
3995308    9      0  
3995309    9      0  

[3995310 rows x 7 columns]

In [4]:
test_day=[0, 1]
train=df[(df['label']==0)&(~df['day'].isin(test_day))][df.columns[:-2]].reset_index(drop=True)
test=df[(df['day'].isin(test_day))][df.columns[:-2]].reset_index(drop=True)
test

original  original_lag1  original_lag2  original_lag3  original_lag4
0           53.6           53.2           52.8           52.8           53.4
1           54.0           53.6           53.2           52.8           52.8
2           54.7           54.0           53.6           53.2           52.8
3           55.7           54.7           54.0           53.6           53.2
4           55.5           55.7           54.7           54.0           53.6
...          ...            ...            ...            ...            ...
719457      46.0           46.1           45.9           45.7           45.6
719458      46.0           46.0           46.1           45.9           45.7
719459      45.9           46.0           46.0           46.1           45.9
719460      45.9           45.9           46.0           46.0           46.1
719461      46.1           45.9           45.9           46.0           46.0

[719462 rows x 5 columns]

In [48]:
##訓練とテストでデータを分ける場合のLOF
# model = LocalOutlierFactor(n_neighbors=500, novelty=True)
# model.fit(train) # train_dataは正常データが大多数であるような訓練データ
# prediction = model.predict(test) # テストデータに対する予測
# score = model.score_samples(test) # テストデータの異常度

In [42]:
#訓練とテストでデータを分けない場合
clf = LocalOutlierFactor(n_neighbors=1001, contamination=0.002)
pred = clf.fit_predict(test)
d=np.where(pred==-1, 1, 0)

In [43]:
# データを改めて用意しない
test_v=df[(df['day'].isin(test_day))][['original', 'label', 'day']]
test_v['d']=d

In [44]:
# # 評価用のデータを改めて用意し、異常度を割り当てる
# test_v=original[original['day'].isin(test_day)][['original', 'label']].reset_index(drop=True)
# test_v['d']=d[0]
# test_v.loc[window-1:, 'd']=d
# d=test_v['d'].values

In [45]:
thr=0.5
precision, recall=validate.validate(test_v, d, thr)
print(f'適合率：{precision}')
print(f'再現率：{recall}')

適合率：0.7546907574704657
再現率：0.6600985221674877


In [46]:
anorm=(d*5)**2
validate.figure(test_v, anorm, d, thr)